Dans ce notebook nous verrons comment utiliser pandas et sqlite3 ensemble 
ainsi que l'impct sur les performances des GroupBy des index dans SQLite3.

In [1]:
import sqlite3
import pandas 

On crée une base de données en mémoire:

In [2]:
!rm test.db
db = sqlite3.connect("test.db") 

On va créer un générateur pour peupler la table de donner artificielle. 
On utilise simplement des entiers et des congruences modulo pour avoir des données variée mais pas trop.

In [3]:
def generateur(size):
    for i in range(size):
        yield (i%1001, i%1003, i%1007)


On peut faire varier la taille du dataset en changeant l'argument du générateur. 
Ici on fait en sorte d'avoir une base de de donnée qui ne tient pas en mémoire, 
pour l'exercice. La génération de la table prend un certain temps

In [4]:
%%time 
db.execute("CREATE TABLE A(x, y, z)") # On crée une table avec 3 colonnes
db.executemany("INSERT INTO A values (?, ?, ?)", generateur(100000000))
db.commit() # La base de donnée fait ~ 2go. 

CPU times: user 1min 47s, sys: 1.11 s, total: 1min 48s
Wall time: 1min 54s


## Pandas et SQL intégration
Il est possible de faire communiquer Pandas et SQL facilement.
Par exemple, pour rappatrier une table SQLite dans une data frame. 
Par contre, attention si la table ne tient pas en mémoire.

In [5]:
df = pandas.read_sql("SELECT * FROM A LIMIT 1000", db) # Charge en mémoire la table (ouch si ça tient pas !) 

In [6]:
df

x    y    z
0      0    0    0
1      1    1    1
2      2    2    2
3      3    3    3
4      4    4    4
..   ...  ...  ...
995  995  995  995
996  996  996  996
997  997  997  997
998  998  998  998
999  999  999  999

[1000 rows x 3 columns]

In [7]:
query = "SELECT x,y,count(*) as Count FROM A GROUP BY x,y"
%time df = pandas.read_sql(query, db)

CPU times: user 1min 9s, sys: 1.6 s, total: 1min 10s
Wall time: 1min 11s


In [8]:
df.pivot_table("Count", columns=["x"], index=["y"])

x     0     1     2     3     4     5     6     7     8     9     ...  991   \
y                                                                 ...         
0      100   100   100   100   100   100   100   100   100   100  ...    99   
1      100   100   100   100   100   100   100   100   100   100  ...   100   
2       99   100   100   100   100   100   100   100   100   100  ...    99   
3      100    99   100   100   100   100   100   100   100   100  ...   100   
4       99   100    99   100   100   100   100   100   100   100  ...    99   
...    ...   ...   ...   ...   ...   ...   ...   ...   ...   ...  ...   ...   
998    100   100   100   100   100   100   100   100   100   100  ...   100   
999    100   100   100   100   100   100   100   100   100   100  ...    99   
1000   100   100   100   100   100   100   100   100   100   100  ...   100   
1001   100   100   100   100   100   100   100   100   100   100  ...    99   
1002   100   100   100   100   100   100   100   100   100   100  ...   100   

x     992   993   994   995   996   997   998   999   1000  
y                                                           
0      100    99   100    99   100    99   100    99   100  
1       99   100    99   100    99   100    99   100    99  
2      100    99   100    99   100    99   100    99   100  
3       99   100    99   100    99   100    99   100    99  
4      100    99   100    99   100    99   100    99   100  
...    ...   ...   ...   ...   ...   ...   ...   ...   ...  
998     99   100    99   100    99   100   100   100   100  
999    100    99   100    99   100    99   100   100   100  
1000    99   100    99   100    99   100    99   100   100  
1001   100    99   100    99   100    99   100    99   100  
1002    99   100    99   100    99   100    99   100    99  

[1003 rows x 1001 columns]

# Query Plan
Il est possible de vérifier le plan d'execution de la requête `SQL`:

In [9]:
print("\n".join(list(map(lambda e:str(e), db.execute('EXPLAIN QUERY PLAN '+query)))))

(6, 0, 0, 'SCAN TABLE A')
(8, 0, 0, 'USE TEMP B-TREE FOR GROUP BY')


SCAN TABLE indique que SQL passe au travers de la table séquentiellement. 
Ici, ce n'est pas un très bon plan de requêtes, à l'aide d'un index, les performances 
pourraient être meilleurs.

In [10]:
db.execute("CREATE INDEX groupby ON A (x,y)") 

In [11]:
print("\n".join(list(map(lambda e:str(e), db.execute('EXPLAIN QUERY PLAN '+query)))))

(6, 0, 0, 'SCAN TABLE A USING COVERING INDEX groupby')


On voit qu'ici le plan de requête utilise l'index pour scanner la table. Ça va pas mal accélérer la requête. 

In [12]:
%time df = pandas.read_sql(query, db) # On gagne pas mal de temps ! Six fois plus rapide avec l'index.

CPU times: user 7.42 s, sys: 360 ms, total: 7.78 s
Wall time: 7.78 s
